In [106]:
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import statistics
from collections import deque
from data import DATA_ROOT
from plotly.subplots import make_subplots
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split

In [2]:
days = [pd.read_csv(DATA_ROOT / "round2" / f"prices_round_2_day_{i}.csv", sep=";") for i in range(-1, 2)]
days[0]

timestamp  ORCHIDS  TRANSPORT_FEES  EXPORT_TARIFF  IMPORT_TARIFF  \
0              0  1200.00             1.5           10.5           -2.0   
1            100  1201.75             1.5            9.5           -2.0   
2            200  1201.75             1.5            9.5           -2.0   
3            300  1201.75             1.5            9.5           -2.0   
4            400  1201.75             1.5            9.5           -2.0   
...          ...      ...             ...            ...            ...   
9996      999600  1227.75             1.4            8.5           -3.0   
9997      999700  1226.75             1.4            8.5           -3.0   
9998      999800  1227.75             1.4            8.5           -3.0   
9999      999900  1228.00             1.4            8.5           -3.0   
10000    1000000  1228.00             1.4            8.5           -3.0   

        SUNLIGHT   HUMIDITY  DAY  
0      2500.0000  79.000000   -1  
1      2499.4197  79.004100   -1  
2      2498.8457  79.008210   -1  
3      2498.2780  79.012340   -1  
4      2497.7166  79.016490   -1  
...          ...        ...  ...  
9996   3901.9530  83.025764   -1  
9997   3901.4612  83.019300   -1  
9998   3900.9720  83.012856   -1  
9999   3900.4849  83.006424   -1  
10000  3900.0000  83.000000   -1  

[10001 rows x 8 columns]

In [3]:
day = days[0]
day["ma_fast"] = day.rolling(window=10)["ORCHIDS"].mean()
day["ma_slow"] = day.rolling(window=50)["ORCHIDS"].mean()

px.line(days[0], y=["ORCHIDS", "ma_fast", "ma_slow"])

In [89]:
X = []
y = []

look_ahead = 50
look_behind = 10

for day in days:
    rows = list(day.itertuples())

    for i, row in enumerate(rows[:-look_ahead]):
        if i < look_behind:
            continue

        features = []
        for j in range(look_behind):
            features.append(rows[i - j - 1].ORCHIDS - rows[i - j].ORCHIDS)
            # features.append((rows[i - j].SUNLIGHT - 2500) / 2500)
            # features.append((rows[i - j].HUMIDITY - 50) / 50)

        X.append(features)
        y.append(int(rows[i + look_ahead].ORCHIDS > row.ORCHIDS))

X = np.array(X)
y = np.array(y)

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.25, random_state=0)

model = LogisticRegression()
model.fit(X_train, y_train)

y_pred = model.predict(X_test)

print(f"Accuracy: {accuracy_score(y_test, y_pred)}")

Accuracy: 0.5234710300429185


In [90]:
for day in days:
    rows = list(day.itertuples())

    X = []
    prices = []

    for i, row in enumerate(rows[:-look_ahead]):
        if i < look_behind:
            continue

        features = []
        for j in range(look_behind):
            features.append(rows[i - j - 1].ORCHIDS - rows[i - j].ORCHIDS)
            # features.append((rows[i - j].SUNLIGHT - 2500) / 2500)
            # features.append((rows[i - j].HUMIDITY - 50) / 50)

        X.append(features)
        prices.append(row.ORCHIDS)

    X = np.array(X)
    y = (model.predict_proba(X)[:, 0] >= 0.6).astype(int)

    fig = make_subplots(specs=[[{"secondary_y": True}]])
    fig.add_trace(go.Scatter(y=prices, name="Price"), secondary_y=False)
    fig.add_trace(go.Scatter(y=y, name="Trend"), secondary_y=True)
    fig.update_layout(title_text=f"Day {rows[0].DAY}")
    fig.show()

In [296]:
class TrendPredictor:
    def __init__(self) -> None:
        self.sunlight_window = deque()
        self.humidity_window = deque()
        self.window_size = 50

        self.too_little_sunlight = 0

    def run(self, row) -> int:
        return row.IMPORT_TARIFF + row.TRANSPORT_FEES

        self.sunlight_window.append(row.SUNLIGHT)
        if len(self.sunlight_window) > self.window_size:
            self.sunlight_window.popleft()

        self.humidity_window.append(row.HUMIDITY)
        if len(self.humidity_window) > self.window_size:
            self.humidity_window.popleft()

        return (self.sunlight_window[0] - self.sunlight_window[-1])*0 + int(self.humidity_window[0] < self.humidity_window[-1])
        if row.SUNLIGHT < 7 * 365:
            self.too_little_sunlight += 1
        else:
            self.too_little_sunlight = 0

        self.window.append(row.SUNLIGHT * row.HUMIDITY)
        if len(self.window) > self.window_size:
            self.window.popleft()

        return int(self.window[0] < self.window[-1])

        production = 1.0

        production *= (1.0 - min(0.04 * (self.too_little_sunlight // 139), 0.04))

        if row.HUMIDITY < 60:
            production *= (1.0 - (60 - row.HUMIDITY) // 5 / 100)
        elif row.HUMIDITY > 80:
            production *= (1.0 - (row.HUMIDITY - 80) // 5 / 100)

        return production

for day in days:
    predictor = TrendPredictor()

    prices = []
    predictions = []

    for row in day.itertuples():
        prices.append(row.ORCHIDS)
        predictions.append(predictor.run(row))

    fig = make_subplots(specs=[[{"secondary_y": True}]])
    fig.add_trace(go.Scatter(y=prices, name="Price"), secondary_y=False)
    fig.add_trace(go.Scatter(y=predictions, name="Trend"), secondary_y=True)
    fig.update_layout(title_text=f"Day {rows[0].DAY}")
    fig.show()

In [301]:
for day in days:
    fig = make_subplots()
    fig.add_trace(go.Scatter(y=day["ORCHIDS"], name="Price"))
    fig.add_trace(go.Scatter(y=day["ORCHIDS"] + day["TRANSPORT_FEES"] + day["IMPORT_TARIFF"], name="Buy from South"))
    fig.add_trace(go.Scatter(y=day["ORCHIDS"] + day["TRANSPORT_FEES"] + day["EXPORT_TARIFF"], name="Sell to South"))
    fig.update_layout(title_text=f"Day {rows[0].DAY}")
    fig.show()